<a href="https://colab.research.google.com/github/kburns/cism_dedalus_2023/blob/main/lecture_5_convection.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Boundary Conditions -- Convection

**Overview:** This notebook describes how to implement boundary conditions in Dedalus via the tau method, and demonstrates this technique for simulating Rayleigh-Benard and spherical convection.

**About Dedalus:** [Dedalus](http://dedalus-project.org) is an open-source Python package for solving partial differential equations (PDEs) using global spectral methods.
These methods provide highly accurate numerical solutions for PDEs with smooth solutions in simple domains like boxes and spheres.
Dedalus implements modern parallel algorithms utilizing sparse polynomial bases, but all with an easy-to-use symbolic interface.
The code is being used in a wide range of fields, often for problems involving fluid dynamics.

**Author:** [Keaton Burns](http://keaton-burns.com)

# Setup

This cell checks if Dedalus is installed and performs some other basic setup.

If Dedalus is not installed and you are using Google Colab, it will automatically be installed.
This may take a few minutes the first time you run the notebook, but subsequent sessions during the next day or so should have the installation cached.
No need to worry about the details -- just execute the cell.

If you are not using Google Colab, follow the installation instructions in the [Dedalus Docs](https://dedalus-project.readthedocs.io/en/latest/pages/installation.html) to install Dedalus locally on your computer.
Installation using conda is typically straightforward for Mac and Linux.
No promises on Windows.
Execute the cell to confirm Dedalus is installed and importable.

In [1]:
# Set environment variables for best performance
%env OMP_NUM_THREADS=1
%env NUMEXPR_MAX_THREADS=1

# Minimize logging output
import logging
logging.disable(logging.DEBUG)

# Check if running on google colab
import os
using_google_colab = bool(os.getenv("COLAB_RELEASE_TAG"))

# Check for Dedalus
try:
    import dedalus.public as de
    print("Dedalus already installed :)")
except:
    print("Dedalus not installed yet.")
    if using_google_colab:
        print("Installing for Google Colab.")
        print()
        # Step 1: Install FFTW
        !apt-get install libfftw3-dev
        !apt-get install libfftw3-mpi-dev
        # Step 2: Set paths for Dedalus installation
        import os
        os.environ['MPI_INCLUDE_PATH'] = "/usr/lib/x86_64-linux-gnu/openmpi/include"
        os.environ['MPI_LIBRARY_PATH'] = "/usr/lib/x86_64-linux-gnu"
        os.environ['FFTW_INCLUDE_PATH'] = "/usr/include"
        os.environ['FFTW_LIBRARY_PATH'] = "/usr/lib/x86_64-linux-gnu"
        # Step 3: Install Dedalus using pip
        !pip3 install cython mpi4py numpy setuptools wheel
        !CC=mpicc pip3 install --no-cache --no-build-isolation dedalus
        # Step 4: Check installation
        print()
        try:
            import dedalus.public as de
            print("Dedalus successfully installed :)")
        except:
            print("Error installing Dedalus :(")
            raise
        # Step 5: Install ipympl and restart kernel
        !pip3 install -q ipympl
        get_ipython().kernel.do_shutdown(restart=True)
    else:
        print("See website for installation instructions:")
        print("https://dedalus-project.readthedocs.io/en/latest/pages/installation.html")

env: OMP_NUM_THREADS=1
env: NUMEXPR_MAX_THREADS=1
Dedalus already installed :)


# Content

First let's import everything we need to run the rest of the notebook.

In [2]:
# Set environment variables for best performance
%env OMP_NUM_THREADS=1
%env NUMEXPR_MAX_THREADS=1

# Minimize logging output
import logging
logging.disable(logging.DEBUG)
logger = logging.getLogger(__name__)

# Check if running on google colab
import os
using_google_colab = bool(os.getenv("COLAB_RELEASE_TAG"))

# Setup interactive matplotlib
if using_google_colab:
    from google.colab import output
    output.enable_custom_widget_manager()

# Import libraries
import numpy as np
import matplotlib.pyplot as plt
import dedalus.public as d3
%matplotlib widget

env: OMP_NUM_THREADS=1
env: NUMEXPR_MAX_THREADS=1


## The Tau Method

So far we've only seen domains that are periodic (or spherical), so we haven't had to deal with imposing boundary conditions.
Boundary conditions are where spectral methods commit their sins, so to speak.

The problem is fundamental: in bounded domains, we seek to represent our solutions with finite-degree polynomials.
But the equations we're trying to solve do not have polynomial solutions, in general.
As a result, any **approximate polynomial** solution to our PDE must actually be an exact solution to a different (but hopefully close) **approximate problem**.

The **tau method** is the approach of explicitly adding a variable modification to the PDE to make it exactly solvable over polynomials.
It can also be viewed as adding degrees of freedom to the system to allow imposing the boundary conditions, similar to how we adding constants to allow imposing gauge constraints.

As an example, let's consider the equation:

$$
\begin{gathered}
        \partial_x u(x) = u(x)\\
        u(0) = 1
\end{gathered}
$$

The exact solution is $`u(x) = e^x$, but we seek an approximate polynomial solution.
The tau method modifies the PDE to be:

$$\partial_x u(x) - u(x) + \tau P(x) = 0$$

where $\tau$ is an undetermined constant and $P(x)$ is a specified polynomial.
If $P(x)$ is a polynomial of degree $N$, then the modified equation also has an exact polynomial solution $u_N(x)$ that is also of degree $N$.
For instance, taking $P(x) = x^2$, the modified PDE has the solution $u_2(x) = (x^2 + 2 x + 2) / 2$ with $\tau = 1 / 2$.

Picking the optimal form of the tau polynomials $P(x)$ is generally an open mathematical problem, but we have some rules of thumb to follow.
For problems with two boundaries (e.g. Chebyshev boxes or spherical shells), it's usually best to write the system with *first-order corrections* using the first ultraspherical polynomials for $P(x)$.
For problems with one boundary (e.g. full disks or balls), it's usually best to write the system using higher-order corrections corresponding to the number of derivatives in the PDE.
There are more details in the ["Tau Method" documentation page](https://dedalus-project.readthedocs.io/en/latest/pages/tau_method.html), but you should basically be able to just copy what we do in the example problems in each geometry.

Ok, enough theory! Let's put this to use to solve Rayleigh-Benard convection in 2D.
First let's set up our domain and fields with a Chebyshev basis.
In addition to the regular variables, we include unknown tau variables that depend on $x$ but not $y$ (they are constant in the wall-normal direction), one for each boundary condition (buoyancy and velocity on top and bottom).
And we have one constant term for the pressure gauge, like before.

In [3]:
# Parameters
Lx, Lz = 4, 1
Nx, Nz = 256, 64
dealias = 3/2
dtype = np.float64

# Bases
coords = d3.CartesianCoordinates('x', 'z')
dist = d3.Distributor(coords, dtype=dtype)
xbasis = d3.RealFourier(coords['x'], size=Nx, bounds=(0, Lx), dealias=dealias)
zbasis = d3.ChebyshevT(coords['z'], size=Nz, bounds=(0, Lz), dealias=dealias)

# Fields
p = dist.Field(name='p', bases=(xbasis,zbasis))
b = dist.Field(name='b', bases=(xbasis,zbasis))
u = dist.VectorField(coords, name='u', bases=(xbasis,zbasis))
tau_p = dist.Field(name='tau_p')
tau_b1 = dist.Field(name='tau_b1', bases=xbasis)
tau_b2 = dist.Field(name='tau_b2', bases=xbasis)
tau_u1 = dist.VectorField(coords, name='tau_u1', bases=xbasis)
tau_u2 = dist.VectorField(coords, name='tau_u2', bases=xbasis)

Next let's get ready to setup the problem.
First, we multiply the tau terms by $P(x)$ using the `lift` operator -- this is just a helper to make it simple to specify which polynomials we want to multiply by -- here's its the last polynomial from the first ultraspherical basis (where the derivative maps Chebyshev polynomials).
We multiply this by the $z$ unit vector and add it to the gradients of our variables, creating *tau modified* versions of $\nabla u$ and $\nabla b$.

In [4]:
# Problem parameters
Rayleigh = 2e6
Prandtl = 1

# Substitutions
kappa = (Rayleigh * Prandtl)**(-1/2)
nu = (Rayleigh / Prandtl)**(-1/2)
x, z = dist.local_grids(xbasis, zbasis)
ex, ez = coords.unit_vector_fields(dist)

# First-order tau terms
lift = lambda A: d3.Lift(A, zbasis.derivative_basis(1), -1)
grad_u = d3.grad(u) + ez*lift(tau_u1) # First-order reduction
grad_b = d3.grad(b) + ez*lift(tau_b1) # First-order reduction

Then we can just enter the equations using these modified first-order variables, as well as adding the second tau terms to the PDEs.
Since we've expanded the system with these tau variables, we now have the freedom to impose the boundary conditions, as well.

In [5]:
# Problem
# First-order form: "div(f)" becomes "trace(grad_f)"
# First-order form: "lap(f)" becomes "div(grad_f)"
problem = d3.IVP([p, b, u, tau_p, tau_b1, tau_b2, tau_u1, tau_u2], namespace=locals())
problem.add_equation("trace(grad_u) + tau_p = 0")
problem.add_equation("dt(b) - kappa*div(grad_b) + lift(tau_b2) = - u@grad(b)")
problem.add_equation("dt(u) - nu*div(grad_u) + grad(p) - b*ez + lift(tau_u2) = - u@grad(u)")
problem.add_equation("b(z=0) = Lz")
problem.add_equation("u(z=0) = 0")
problem.add_equation("b(z=Lz) = 0")
problem.add_equation("u(z=Lz) = 0")
problem.add_equation("integ(p) = 0"); # Pressure gauge

Then we build the solver and set initial conditions (conductive state plus some noise to kick off the instability):

In [6]:
# Solver parameters
stop_sim_time = 30
timestepper = d3.RK222
max_timestep = 0.125

# Solver
solver = problem.build_solver(timestepper)
solver.stop_sim_time = stop_sim_time

# Initial conditions
b.fill_random('g', seed=42, distribution='normal', scale=1e-3) # Random noise
b['g'] *= z * (Lz - z) # Damp noise at walls
b['g'] += Lz - z # Add linear background

2025-10-07 23:25:29,909 subsystems 0/1 INFO :: Building subproblem matrices 1/128 (~1%) Elapsed: 0s, Remaining: 17s, Rate: 7.6e+00/s
2025-10-07 23:25:30,422 subsystems 0/1 INFO :: Building subproblem matrices 13/128 (~10%) Elapsed: 1s, Remaining: 6s, Rate: 2.0e+01/s
2025-10-07 23:25:30,979 subsystems 0/1 INFO :: Building subproblem matrices 26/128 (~20%) Elapsed: 1s, Remaining: 5s, Rate: 2.2e+01/s
2025-10-07 23:25:31,534 subsystems 0/1 INFO :: Building subproblem matrices 39/128 (~30%) Elapsed: 2s, Remaining: 4s, Rate: 2.2e+01/s
2025-10-07 23:25:32,089 subsystems 0/1 INFO :: Building subproblem matrices 52/128 (~41%) Elapsed: 2s, Remaining: 3s, Rate: 2.2e+01/s
2025-10-07 23:25:32,643 subsystems 0/1 INFO :: Building subproblem matrices 65/128 (~51%) Elapsed: 3s, Remaining: 3s, Rate: 2.3e+01/s
2025-10-07 23:25:33,197 subsystems 0/1 INFO :: Building subproblem matrices 78/128 (~61%) Elapsed: 3s, Remaining: 2s, Rate: 2.3e+01/s
2025-10-07 23:25:33,803 subsystems 0/1 INFO :: Building subprob

Then we can add analysis tasks and the CFL handler and run the simulation (it should take about a minute):

In [7]:
# Analysis
snapshots = solver.evaluator.add_file_handler('snapshots_rbc', sim_dt=0.25)
snapshots.add_task(b, name='buoyancy')
snapshots.add_task(-d3.div(d3.skew(u)), name='vorticity')

# CFL
CFL = d3.CFL(solver, initial_dt=max_timestep, cadence=10, safety=0.5, threshold=0.05,
             max_change=1.5, min_change=0.5, max_dt=max_timestep)
CFL.add_velocity(u)

# Main loop
try:
    logger.info('Starting main loop')
    while solver.proceed:
        timestep = CFL.compute_timestep()
        solver.step(timestep)
        if (solver.iteration-1) % 100 == 0:
            logger.info('Iteration=%i, Time=%e, dt=%e' %(solver.iteration, solver.sim_time, timestep))
except:
    logger.error('Exception raised, triggering end of main loop.')
    raise
finally:
    solver.log_stats()

2025-10-07 23:25:35,476 __main__ 0/1 INFO :: Starting main loop
2025-10-07 23:25:37,197 __main__ 0/1 INFO :: Iteration=1, Time=1.250000e-01, dt=1.250000e-01
2025-10-07 23:25:41,391 __main__ 0/1 INFO :: Iteration=101, Time=1.200000e+01, dt=6.250000e-02
2025-10-07 23:25:47,079 __main__ 0/1 INFO :: Iteration=201, Time=1.347285e+01, dt=9.529498e-03
2025-10-07 23:25:51,388 __main__ 0/1 INFO :: Iteration=301, Time=1.428005e+01, dt=7.590742e-03
2025-10-07 23:25:55,436 __main__ 0/1 INFO :: Iteration=401, Time=1.505677e+01, dt=8.692447e-03
2025-10-07 23:25:58,986 __main__ 0/1 INFO :: Iteration=501, Time=1.592602e+01, dt=8.692447e-03
2025-10-07 23:26:03,208 __main__ 0/1 INFO :: Iteration=601, Time=1.690597e+01, dt=1.059792e-02
2025-10-07 23:26:07,321 __main__ 0/1 INFO :: Iteration=701, Time=1.795175e+01, dt=1.028154e-02
2025-10-07 23:26:11,314 __main__ 0/1 INFO :: Iteration=801, Time=1.902003e+01, dt=1.145797e-02
2025-10-07 23:26:15,555 __main__ 0/1 INFO :: Iteration=901, Time=2.017117e+01, dt=1

And let's make a movie of the output:

In [8]:

import matplotlib
from matplotlib import animation
from IPython.display import HTML
import h5py

# Plot parameters
cmap = plt.cm.RdBu_r
dpi = 100
figsize = (6, 6)
fps = 20

# Create figure
with h5py.File('snapshots_rbc/snapshots_rbc_s1.h5', mode='r') as file:
    fig, ax = plt.subplots(2, 1, figsize=(8, 6), dpi=80)
    b = file['tasks']['buoyancy']
    w = file['tasks']['vorticity']
    x = b.dims[1][0][:].ravel()
    y = b.dims[2][0][:].ravel()
    b_clim = np.max(np.abs(b))
    w_clim = np.max(np.abs(w))
    b_im = ax[0].pcolormesh(x, y, b[0].T, clim=(-b_clim, b_clim), cmap=cmap)
    ax[0].set_aspect('equal')
    ax[0].set_title("Buoyancy")
    w_im = ax[1].pcolormesh(x, y, w[0].T, clim=(-w_clim, w_clim), cmap=cmap)
    ax[1].set_aspect('equal')
    ax[1].set_title("Vorticity")
    plt.tight_layout()
    def animate(i):
        b_im.set_array(b[i].T.ravel())
        w_im.set_array(w[i].T.ravel())
        return (b_im, w_im)
    anim = animation.FuncAnimation(fig, animate, frames=b.shape[0], interval=1000//fps, blit=True)
    video_rbc = HTML(anim.to_html5_video())
    plt.close(fig)

2025-10-07 23:26:51,899 matplotlib.animation 0/1 INFO :: Animation.save using <class 'matplotlib.animation.FFMpegWriter'>
2025-10-07 23:26:51,901 matplotlib.animation 0/1 INFO :: MovieWriter._run: running command: ffmpeg -f rawvideo -vcodec rawvideo -s 640x480 -pix_fmt rgba -framerate 20.0 -i pipe: -vcodec h264 -pix_fmt yuv420p -y /var/folders/gl/8q1_pm2s1490lvyfvm_8yby80000gn/T/tmpq4qtm8iv/temp.m4v


In [9]:
video_rbc.data = video_rbc.data.replace('autoplay', '')
video_rbc

## Spherical Convection

So there's a bit of syntax to get things sorted with the tau terms, but since the code is now vectorial and only has a few references to the domain coordinates (e.g. in the BC specification), this code is highly portable and easy to apply to other geometries.
Let's quickly do Rayleigh-Benard in a spherical shell.

First the domain and fields just like before, but now using the shell's surface (S2) for the tau variables:

In [10]:
# Parameters
Ri, Ro = 14, 15
Nphi, Ntheta, Nr = 128, 64, 8
dealias = 3/2
dtype = np.float64
mesh = None

# Bases
coords = d3.SphericalCoordinates('phi', 'theta', 'r')
dist = d3.Distributor(coords, dtype=dtype, mesh=mesh)
shell = d3.ShellBasis(coords, shape=(Nphi, Ntheta, Nr), radii=(Ri, Ro), dealias=dealias, dtype=dtype)
sphere = shell.outer_surface

# Fields
p = dist.Field(name='p', bases=shell)
b = dist.Field(name='b', bases=shell)
u = dist.VectorField(coords, name='u', bases=shell)
tau_p = dist.Field(name='tau_p')
tau_b1 = dist.Field(name='tau_b1', bases=sphere)
tau_b2 = dist.Field(name='tau_b2', bases=sphere)
tau_u1 = dist.VectorField(coords, name='tau_u1', bases=sphere)
tau_u2 = dist.VectorField(coords, name='tau_u2', bases=sphere)

And now the problem parameters, substitutions, and first-order tau terms as before, but just using the radial vector instead of the z unit vector:

In [11]:
# Problem parameters
Rayleigh = 3500
Prandtl = 1

# Substitutions
kappa = (Rayleigh * Prandtl)**(-1/2)
nu = (Rayleigh / Prandtl)**(-1/2)
phi, theta, r = dist.local_grids(shell)
er = dist.VectorField(coords, bases=shell.radial_basis)
er['g'][2] = 1
rvec = dist.VectorField(coords, bases=shell.radial_basis)
rvec['g'][2] = r

# First-order tau terms
lift = lambda A: d3.Lift(A, shell.derivative_basis(1), -1)
grad_u = d3.grad(u) + rvec*lift(tau_u1) # First-order reduction
grad_b = d3.grad(b) + rvec*lift(tau_b1) # First-order reduction

Now the PDE specification is exactly the same as before, just with $z$ replaced by $r$ in the gravity term and the BCs:

In [12]:
# Problem
problem = d3.IVP([p, b, u, tau_p, tau_b1, tau_b2, tau_u1, tau_u2], namespace=locals())
problem.add_equation("trace(grad_u) + tau_p = 0")
problem.add_equation("dt(b) - kappa*div(grad_b) + lift(tau_b2) = - u@grad(b)")
problem.add_equation("dt(u) - nu*div(grad_u) + grad(p) - b*er + lift(tau_u2) = - u@grad(u)")
problem.add_equation("b(r=Ri) = 1")
problem.add_equation("u(r=Ri) = 0")
problem.add_equation("b(r=Ro) = 0")
problem.add_equation("u(r=Ro) = 0")
problem.add_equation("integ(p) = 0"); # Pressure gauge

Then we build the solver and set initial conditions, again just like before:

In [13]:
# Solver parameters
stop_sim_time = 2000
timestepper = d3.SBDF2
max_timestep = 1

# Solver
solver = problem.build_solver(timestepper)
solver.stop_sim_time = stop_sim_time

# Initial conditions
b.fill_random('g', seed=42, distribution='normal', scale=1e-3) # Random noise
b['g'] *= (r - Ri) * (Ro - r) # Damp noise at walls
b['g'] += (Ri - Ri*Ro/r) / (Ri - Ro) # Add linear background

2025-10-07 23:28:32,103 subsystems 0/1 INFO :: Building subproblem matrices 1/63 (~2%) Elapsed: 0s, Remaining: 21s, Rate: 3.0e+00/s
2025-10-07 23:28:35,331 subsystems 0/1 INFO :: Building subproblem matrices 7/63 (~11%) Elapsed: 4s, Remaining: 29s, Rate: 2.0e+00/s
2025-10-07 23:28:39,177 subsystems 0/1 INFO :: Building subproblem matrices 14/63 (~22%) Elapsed: 7s, Remaining: 26s, Rate: 1.9e+00/s
2025-10-07 23:28:41,851 subsystems 0/1 INFO :: Building subproblem matrices 18/63 (~29%) Elapsed: 10s, Remaining: 25s, Rate: 1.8e+00/s
2025-10-07 23:28:43,577 subsystems 0/1 INFO :: Building subproblem matrices 21/63 (~33%) Elapsed: 12s, Remaining: 24s, Rate: 1.8e+00/s
2025-10-07 23:28:47,634 subsystems 0/1 INFO :: Building subproblem matrices 28/63 (~44%) Elapsed: 16s, Remaining: 20s, Rate: 1.8e+00/s
2025-10-07 23:28:51,636 subsystems 0/1 INFO :: Building subproblem matrices 35/63 (~56%) Elapsed: 20s, Remaining: 16s, Rate: 1.8e+00/s
2025-10-07 23:28:52,217 subsystems 0/1 INFO :: Building subpr

And finally just analysis, CFL, and the main loop.
The full simulation here is slower -- it takes about 10 minutes to run, so we'll skip the simulation for the notebook and just show the movie of the result:

In [14]:
# Analysis
flux = er @ (-kappa*d3.grad(b) + u*b)
snapshots = solver.evaluator.add_file_handler('snapshots_shell', sim_dt=10, max_writes=10)
snapshots.add_task(b(r=(Ri+Ro)/2), scales=dealias, name='bmid')
snapshots.add_task(flux(r=Ro), scales=dealias, name='flux_r_outer')
snapshots.add_task(flux(r=Ri), scales=dealias, name='flux_r_inner')
snapshots.add_task(flux(phi=0), scales=dealias, name='flux_phi_start')
snapshots.add_task(flux(phi=3*np.pi/2), scales=dealias, name='flux_phi_end')

# CFL
CFL = d3.CFL(solver, initial_dt=max_timestep, cadence=10, safety=2, threshold=0.1,
             max_change=1.5, min_change=0.5, max_dt=max_timestep)
CFL.add_velocity(u)

# Main loop
# try:
#     logger.info('Starting main loop')
#     while solver.proceed:
#         timestep = CFL.compute_timestep()
#         solver.step(timestep)
#         if (solver.iteration-1) % 10 == 0:
#             logger.info('Iteration=%i, Time=%e, dt=%e' %(solver.iteration, solver.sim_time, timestep))
# except:
#     logger.error('Exception raised, triggering end of main loop.')
#     raise
# finally:
#     solver.log_stats()

In [15]:
from IPython.display import Video
Video("shell.mp4", embed=True, width=600)